In [1]:
import pandas as pd

#df = pd.read_csv('C:\GitHub/rag\metrics\data.csv')
df = pd.read_csv('C:/GitHub/rag/metrics/data_extra_temp.csv')

df

total_predictors  community_prediction  \
0           0.097902                  0.14   
1           0.097902                  0.15   
2           0.090909                  0.38   
3           0.671329                  0.99   
4           0.125874                  0.54   
..               ...                   ...   
92          0.140057                  0.97   
93          0.132867                  0.65   
94          0.125874                  0.83   
95          0.132867                  0.30   
96          0.140057                  0.68   

                                             articles  mean_ACE  \
0   [{'id': 83, 'url': 'https://www.thelancet.com/...  0.306112   
1   [{'id': 69, 'url': 'https://tools.cdc.gov/podc...  0.076705   
2   [{'id': 43, 'url': 'https://menafn.com/arabic/...  0.232543   
3   [{'id': 99, 'url': 'https://www.cnn.com/2023/0...  0.374007   
4   [{'id': 41, 'url': 'https://economictimes.indi...  0.212494   
..                                                ...       ...   
92  [{'id': 4, 'url': 'https://abcnews.go.com/Busi...  0.264816   
93  [{'id': 15, 'url': 'https://www.independent.co...  0.219757   
94  [{'id': 17, 'url': 'https://www.irishtimes.com...  0.184166   
95  [{'id': 36, 'url': 'https://news.yahoo.com/fed...  0.164507   
96  [{'id': 36, 'url': 'https://www.thenews.com.pk...  0.225550   

                                             question  answer        date  \
0   Will the CDC's assessment of the risk posed by...       1  2024-08-24   
1   Will the CDC's assessment of the risk posed by...       0  2024-08-24   
2   Will Greg Brockman return to OpenAI following ...       0  2024-08-24   
3   Will Robert F. Kennedy Jr. suspend his 2024 pr...       1  2024-08-24   
4   Will the Warren Buffett Indicator exceed 200% ...       0  2024-08-21   
..                                                ...     ...         ...   
92  Will Linda Yaccarino be the CEO of X on April ...       1  2024-05-31   
93  Will Keir Starmer's approval rating as Prime M...       1  2024-08-17   
94  Will Keir Starmer's approval rating as Prime M...       1  2024-08-17   
95  Will the Fed hold rates steady at their Septem...       0  2024-08-23   
96         Will NVIDIA's stock price rise in Q4 2023?       1  2023-12-01   

    PlainLLM_0  PlainLLM_1  PlainLLM_2  ... HybridRAG_lc_1  \
0        0.400        0.70        0.30  ...          0.800   
1        0.300        0.22        0.60  ...          0.200   
2        0.250        0.65        0.30  ...          0.900   
3        0.205        0.35        0.32  ...          0.857   
4        0.600        0.06        0.35  ...          0.500   
..         ...         ...         ...  ...            ...   
92       0.350        0.80        0.20  ...          1.000   
93       0.720        0.52        0.58  ...          0.710   
94       0.850        0.85        0.85  ...          0.850   
95       0.675        0.48        0.62  ...          0.500   
96       0.625        0.60        0.58  ...          0.700   

                                  HybridRAG_lc_1_text HybridRAG_lc_2  \
0   The recent surge in mpox cases in Africa, comb...           0.60   
1   Low probability of a CDC assessment exceeding ...           0.15   
2   Greg Brockman has already stated his intention...           0.80   
3   Given the recent information and the provided ...           0.95   
4   Given the current level of the Buffett Indicat...           0.87   
..                                                ...            ...   
92  Linda Yaccarino has already been confirmed by ...           1.00   
93  Keir Starmer's approval rating among ethnicall...           0.74   
94  The Labour Party is leading in the polls, and ...           0.80   
95  Recent inflation data has remained stubborn, a...           0.60   
96  Based on the strong AI demand and NVIDIA's pos...           0.67   

                                  HybridRAG_lc_2_text HybridRAG_gd_1  \
0   Given the low risk assessment by HH

In [2]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 97 entries, 0 to 96
Data columns (total 37 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   total_predictors               97 non-null     float64
 1   community_prediction           97 non-null     float64
 2   articles                       97 non-null     object 
 3   mean_ACE                       97 non-null     float64
 4   question                       97 non-null     object 
 5   answer                         97 non-null     int64  
 6   date                           97 non-null     object 
 7   PlainLLM_0                     97 non-null     float64
 8   PlainLLM_1                     97 non-null     float64
 9   PlainLLM_2                     97 non-null     float64
 10  PlainLLM_2_text                97 non-null     object 
 11  NaiveRAG_gd_0                  97 non-null     float64
 12  NaiveRAG_gd_0_text             97 non-null     objec

In [3]:
import os

import nest_asyncio
nest_asyncio.apply()

os.chdir("../app")  # Adjust the path based on your folder structure

from rag_pipelines import AsyncBinaryQuestionPlainLLM, AsyncBinaryQuestionNaiveRAG, AsyncBinaryQuestionRAG_hybrid_crossencoder, AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT
from tqdm import tqdm
import asyncio

In [ ]:
col = 'PlainLLM_2'
text = "PlainLLM_2_text"


df[col] = None
df[text] = None

model = AsyncBinaryQuestionPlainLLM()
num_retries = 3

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):

        for attempt in range(num_retries):
            try:
                anwser = await model.run(row['question'])
                df.at[index, col] = anwser.probability / 100
                df.at[index, text] = anwser.justification
                break  # Exit the retry loop if successful
            except Exception as e:
                print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                if attempt == num_retries - 1:
                    df.at[index, col] = None
                    df.at[index, text] = None
                await asyncio.sleep(1)

# Run the asynchronous function
await process_rows()

In [ ]:
df.to_csv('C:\GitHub/rag\metrics\data_temp.csv', index=False)

In [ ]:
col = 'NaiveRAG_gd_0'
text = "NaiveRAG_gd_0_text"


#df[col] = None
#df[text] = None

model = AsyncBinaryQuestionNaiveRAG()
num_retries = 3

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):
        if index != 0:
            continue

        for attempt in range(num_retries):
            try:
                anwser = await model.run(row['question'], date=row['date'])
                df.at[index, col] = anwser.probability / 100
                df.at[index, text] = anwser.justification
                break  # Exit the retry loop if successful
            except Exception as e:
                print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                if attempt == num_retries - 1:
                    df.at[index, col] = None
                    df.at[index, text] = None
                await asyncio.sleep(1)
        
        df.to_csv('C:\GitHub/rag\metrics\data_extra_temp.csv', index=False)

# Run the asynchronous function
asyncio.run(process_rows())

In [ ]:
col = 'NaiveRAG_gd_1'
text = "NaiveRAG_gd_1_text"


df[col] = None
df[text] = None

model = AsyncBinaryQuestionNaiveRAG()
num_retries = 3

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):
        #if index != 0:
        #    continue

        for attempt in range(num_retries):
            try:
                anwser = await model.run(row['question'], date=row['date'])
                df.at[index, col] = anwser.probability / 100
                df.at[index, text] = anwser.justification
                break  # Exit the retry loop if successful
            except Exception as e:
                print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                if attempt == num_retries - 1:
                    df.at[index, col] = None
                    df.at[index, text] = None
                await asyncio.sleep(1)
        
        df.to_csv('C:\GitHub/rag\metrics\data_extra_temp.csv', index=False)

# Run the asynchronous function
asyncio.run(process_rows())

In [ ]:
col = 'NaiveRAG_gd_2'
text = "NaiveRAG_gd_2_text"


#df[col] = None
#df[text] = None

model = AsyncBinaryQuestionNaiveRAG()
num_retries = 3

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):
        if index < 89:
            continue

        for attempt in range(num_retries):
            try:
                anwser = await model.run(row['question'], date=row['date'])
                df.at[index, col] = anwser.probability / 100
                df.at[index, text] = anwser.justification
                break  # Exit the retry loop if successful
            except Exception as e:
                print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                if attempt == num_retries - 1:
                    df.at[index, col] = None
                    df.at[index, text] = None
                await asyncio.sleep(1)
        
        df.to_csv('C:\GitHub/rag\metrics\data_extra_temp.csv', index=False)

# Run the asynchronous function
asyncio.run(process_rows())

In [ ]:
col = 'NaiveRAG_lc_0'
text = "NaiveRAG_lc_0_text"


df[col] = None
df[text] = None

model = AsyncBinaryQuestionNaiveRAG()
num_retries = 3

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):
        #if index != 0:
        #    continue

        for attempt in range(num_retries):
            try:
                articles = eval(row['articles'])
                anwser = await model.run(row['question'], data=articles)
                df.at[index, col] = anwser.probability / 100
                df.at[index, text] = anwser.justification
                break  # Exit the retry loop if successful
            except Exception as e:
                print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                if attempt == num_retries - 1:
                    df.at[index, col] = None
                    df.at[index, text] = None
                await asyncio.sleep(1)
        
        df.to_csv('C:\GitHub/rag\metrics\data_extra_temp.csv', index=False)

# Run the asynchronous function
asyncio.run(process_rows())

In [ ]:
col = 'NaiveRAG_lc_2'
text = "NaiveRAG_lc_2_text"

#df[col] = None
#df[text] = None

model = AsyncBinaryQuestionNaiveRAG()
num_retries = 3

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):
        if index < 66:
            continue

        for attempt in range(num_retries):
            try:
                articles = eval(row['articles'])
                anwser = await model.run(row['question'], data=articles)
                df.at[index, col] = anwser.probability / 100
                df.at[index, text] = anwser.justification
                break  # Exit the retry loop if successful
            except Exception as e:
                print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                if attempt == num_retries - 1:
                    df.at[index, col] = None
                    df.at[index, text] = None
                await asyncio.sleep(1)
        
        df.to_csv('C:\GitHub/rag\metrics\data_extra_temp.csv', index=False)

# Run the asynchronous function
asyncio.run(process_rows())

In [ ]:
import numpy as np

col = 'NaiveRAG_lc_2'
text = "NaiveRAG_lc_2_text"


#df[col] = None
#df[text] = None

model = AsyncBinaryQuestionNaiveRAG()
num_retries = 3

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):
        if index != 67:
            continue

        for attempt in range(num_retries):
            try:
                articles = eval(row['articles'])
                anwser = await model.run(row['question'], data=articles)
                df.at[index, col] = anwser.probability / 100
                df.at[index, text] = anwser.justification
                break  # Exit the retry loop if successful
            except Exception as e:
                print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                if attempt == num_retries - 1:
                    df.at[index, col] = None
                    df.at[index, text] = None
                await asyncio.sleep(20)
        
        df.to_csv('C:\GitHub/rag\metrics\data_extra_temp.csv', index=False)

# Run the asynchronous function
asyncio.run(process_rows())

In [ ]:
df.head()

In [ ]:
df.to_csv('C:\GitHub/rag\metrics\data_temp.csv', index=False)

In [ ]:
col = 'HybridRAG_lc_0'
text = "HybridRAG_lc_0_text"


#df[col] = None
#df[text] = None

model = AsyncBinaryQuestionRAG_hybrid_crossencoder()
num_retries = 3

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):
        if index < 41:
            continue

        for attempt in range(num_retries):
            try:
                articles = eval(row['articles'])
                anwser = await model.run(row['question'], data=articles)
                df.at[index, col] = anwser.probability / 100
                df.at[index, text] = anwser.justification
                break  # Exit the retry loop if successful
            except Exception as e:
                print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                if attempt == num_retries - 1:
                    df.at[index, col] = None
                    df.at[index, text] = None
                await asyncio.sleep(1)
        
        df.to_csv('C:\GitHub/rag\metrics\data_extra_temp.csv', index=False)

# Run the asynchronous function
asyncio.run(process_rows())

In [ ]:
import numpy as np

col = 'HybridRAG_lc_1'
text = "HybridRAG_lc_1_text"


#df[col] = None
#df[text] = None

model = AsyncBinaryQuestionRAG_hybrid_crossencoder()
num_retries = 3

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):
        #if index < 41:
        #    continue

        if not np.isnan(df.at[index, col]):
            print(f"Skipping index {index} as it is already processed.")
            pass
        else:
            print(f"Processing index {index}...")

            for attempt in range(num_retries):
                try:
                    articles = eval(row['articles'])
                    anwser = await model.run(row['question'], data=articles)
                    df.at[index, col] = anwser.probability / 100
                    df.at[index, text] = anwser.justification
                    break  # Exit the retry loop if successful
                except Exception as e:
                    print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                    if attempt == num_retries - 1:
                        df.at[index, col] = None
                        df.at[index, text] = None
                    await asyncio.sleep(1)
            
            df.to_csv('C:\GitHub/rag\metrics\data_extra_temp.csv', index=False)

# Run the asynchronous function
asyncio.run(process_rows())

In [ ]:
col = 'HybridRAG_lc_2'
text = "HybridRAG_lc_2_text"


#df[col] = None
#df[text] = None

model = AsyncBinaryQuestionRAG_hybrid_crossencoder()
num_retries = 3

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):
        #if index < 41:
        #    continue

        if not np.isnan(df.at[index, col]):
            print(f"Skipping index {index} as it is already processed.")
            pass
        else:
            print(f"Processing index {index}...")

            for attempt in range(num_retries):
                try:
                    articles = eval(row['articles'])
                    anwser = await model.run(row['question'], data=articles)
                    df.at[index, col] = anwser.probability / 100
                    df.at[index, text] = anwser.justification
                    break  # Exit the retry loop if successful
                except Exception as e:
                    print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                    if attempt == num_retries - 1:
                        df.at[index, col] = None
                        df.at[index, text] = None
                    await asyncio.sleep(1)
            
            df.to_csv('C:\GitHub/rag\metrics\data_extra_temp.csv', index=False)

# Run the asynchronous function
asyncio.run(process_rows())

In [ ]:
col = 'HybridRAG_gd_0'
text = "HybridRAG_gd_0_text"


#df[col] = None
#df[text] = None

model = AsyncBinaryQuestionRAG_hybrid_crossencoder()
num_retries = 3

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):
        #if index < 41:
        #    continue

        if not np.isnan(df.at[index, col]):
            print(f"Skipping index {index} as it is already processed.")
            pass
        else:
            print(f"Processing index {index}...")

            for attempt in range(num_retries):
                try:
                    articles = eval(row['articles'])
                    anwser = await model.run(row['question'], data=articles)
                    df.at[index, col] = anwser.probability / 100
                    df.at[index, text] = anwser.justification
                    break  # Exit the retry loop if successful
                except Exception as e:
                    print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                    if attempt == num_retries - 1:
                        df.at[index, col] = None
                        df.at[index, text] = None
                    await asyncio.sleep(1)
            
            df.to_csv('C:\GitHub/rag\metrics\data_extra_temp.csv', index=False)

# Run the asynchronous function
asyncio.run(process_rows())

In [ ]:
col = 'HybridRAG_gd_1'
text = "HybridRAG_gd_1_text"


df[col] = None
df[text] = None

model = AsyncBinaryQuestionRAG_hybrid_crossencoder()
num_retries = 3

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):
        #if index < 40:
        #    continue

        for attempt in range(num_retries):
            try:
                articles = eval(row['articles'])
                anwser = await model.run(row['question'], date = row['date'])
                df.at[index, col] = anwser.probability / 100
                df.at[index, text] = anwser.justification
                break  # Exit the retry loop if successful
            except Exception as e:
                print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                if attempt == num_retries - 1:
                    df.at[index, col] = None
                    df.at[index, text] = None
                await asyncio.sleep(1)
        
        df.to_csv('C:\GitHub/rag\metrics\data_extra_temp.csv', index=False)

# Run the asynchronous function
asyncio.run(process_rows())

In [ ]:
col = 'HybridRAG_gd_2'
text = "HybridRAG_gd_2_text"


df[col] = None
df[text] = None

model = AsyncBinaryQuestionRAG_hybrid_crossencoder()
num_retries = 3

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):
        #if index < 40:
        #    continue

        for attempt in range(num_retries):
            try:
                articles = eval(row['articles'])
                anwser = await model.run(row['question'], date = row['date'])
                df.at[index, col] = anwser.probability / 100
                df.at[index, text] = anwser.justification
                break  # Exit the retry loop if successful
            except Exception as e:
                print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                if attempt == num_retries - 1:
                    df.at[index, col] = None
                    df.at[index, text] = None
                await asyncio.sleep(1)
        
        df.to_csv('C:\GitHub/rag\metrics\data_extra_temp.csv', index=False)

# Run the asynchronous function
asyncio.run(process_rows())

In [ ]:
col = 'HybridRAG_CoT_lc_0'
text = "HybridRAG_CoT_lc_0_text"
reason_con = "HybridRAG_CoT_lc_0_reason_con"
reason_pro = "HybridRAG_CoT_lc_0_reason_pro"


df[col] = None
df[text] = None
df[reason_con] = None
df[reason_pro] = None

model = AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT()
num_retries = 1

async def process_rows():
    for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Processing rows"):
        #if index != 0:
        #    continue

        for attempt in range(num_retries):
            try:
                articles = eval(row['articles'])
                res, rsn_pro, rsn_con = await model.run(row['question'], data = articles)
                anwser = res
                df.at[index, col] = anwser.probability / 100
                df.at[index, text] = anwser.justification
                df.at[index, reason_con] = rsn_con
                df.at[index, reason_pro] = rsn_pro
                break  # Exit the retry loop if successful
            except Exception as e:
                print(f"Attempt {attempt + 1} failed for index {index}: {e}")
                if attempt == num_retries - 1:
                    df.at[index, col] = None
                    df.at[index, text] = None
                await asyncio.sleep(1)
        
        df.to_csv('C:\GitHub/rag\metrics\data_extra_temp.csv', index=False)

# Run the asynchronous function
asyncio.run(process_rows())

2025-05-24 13:56:52,275 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Initializing AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT with model llama-3.1-8b-instant
2025-05-24 13:56:52,276 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Initializing AsyncBinaryQuestionRAG_hybrid_crossencoder
2025-05-24 13:56:52,276 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Initializing dense encoder
2025-05-24 13:56:52,279 | INFO | sentence_transformers.SentenceTransformer | Use pytorch device_name: cpu
2025-05-24 13:56:52,280 | INFO | sentence_transformers.SentenceTransformer | Load pretrained SentenceTransformer: all-MiniLM-L6-v2
2025-05-24 13:56:52,284 | DEBUG | urllib3.connectionpool | Starting new HTTPS connection (1): huggingface.co:443
2025-05-24 13:56:57,745 | DEBUG | urllib3.connectionpool | https://huggingface.co:443 "HEAD /sentence-transformers/all-MiniLM-L6-v2/resolve/main/modules.json HTTP/1.1" 200 0
2025-05-24 13

Processing rows:   0%|          | 0/97 [00:00<?, ?it/s]

2025-05-24 13:57:01,421 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Starting hybrid RAG pipeline for query: 'Will the CDC's assessment of the risk posed by mpox to the US general public exceed "Very Low" before October 1, 2024?'
2025-05-24 13:57:01,421 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | STEP 1: Acquiring data
2025-05-24 13:57:01,423 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Using provided local data
2025-05-24 13:57:01,423 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Retrieving data from local articles for query: 'Will the CDC's assessment of the risk posed by mpox to the US general public exceed "Very Low" before October 1, 2024?'
2025-05-24 13:57:01,424 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Extracted 100 articles from local data
2025-05-24 13:57:01,424 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Data ac

Batches:   0%|          | 0/41 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

2025-05-24 17:52:47,827 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Dense encoding complete: 1178 vectors generated
2025-05-24 17:52:47,828 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Creating sparse embeddings with TF-IDF encoder
2025-05-24 17:52:47,983 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Sparse encoding complete: (1178, 6844) vectors generated
2025-05-24 17:52:47,988 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | STEP 4: Building indices
2025-05-24 17:52:47,988 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Building dense index
2025-05-24 17:52:47,988 | INFO | indexing.index | Building index...
2025-05-24 17:52:47,993 | INFO | indexing.index | Index built successfully.
2025-05-24 17:52:47,994 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Building sparse index
2025-05-24 17:52:47,995 | INFO | indexing.index | Building i

Processing rows:  59%|█████▉    | 57/97 [3:55:50<36:34:33, 3291.84s/it]

2025-05-24 17:52:52,195 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Starting hybrid RAG pipeline for query: 'Will the CDC confirm a case of Clade I mpox in a US resident before August 23, 2024?'
2025-05-24 17:52:52,195 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | STEP 1: Acquiring data
2025-05-24 17:52:52,196 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Using provided local data
2025-05-24 17:52:52,197 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Retrieving data from local articles for query: 'Will the CDC confirm a case of Clade I mpox in a US resident before August 23, 2024?'
2025-05-24 17:52:52,197 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Extracted 100 articles from local data
2025-05-24 17:52:52,198 | INFO | rag_pipelines.AsyncBinaryQuestionRAG_hybrid_crossencoder_CoT | Data acquisition complete. Total texts: 100
2025-05-24 17:52:52,198 | INFO 

Batches:   0%|          | 0/38 [00:00<?, ?it/s]